In [1]:
# Path hack
import os
# change directory from the current Analysis folder to the top level folder for easier navigation
os.chdir('../')
# confirm we're at /RedditTextAnalysis
print(os.getcwd())

/Users/prcork/MiscDataProjects/collaboration/RedditTextAnalysis


In [2]:
# import reddit api wrapper
import praw
import pandas as pd
from textblob import TextBlob
import altair as alt

### Reddit API Instance

In [3]:
# access password and client secret id via local files
with open('pw.txt', 'r') as file1:
    pw = file1.read()

with open('client_secret.txt', 'r') as file2:
    cs = file2.read()

In [4]:
# create a praw Reddit instance with app credentials and secret info passed through
reddit = praw.Reddit(
    client_id="XbesrQBvKymjgLdgg_D6lA",
    client_secret=cs,
    user_agent="NFLTextAnalysis/0.0.1",
    username="ta_api",
    password=pw
)

In [5]:
# create a praw Submission instance for the NO-TN game thread and confirm the correct thread via title
submission = reddit.submission("qtuqqs")
submission.title

'Game Thread: New Orleans Saints (5-3) at Tennessee Titans (7-2)'

### Create Comments Dataframe

### Test Function Implementation at the individual gamethread level

In [6]:
# note that the %load_ext autoreload line only needs to be be run once
%load_ext autoreload

In [7]:
# by including this autoreload command, we only need to re-import Spatial_Joins if we make/save changes to the original py file
%autoreload
from nfl_gamethreads import nfl_gamethreads

In [9]:
NO_TN_list = nfl_gamethreads.get_comments(reddit, 'qtuqqs')
len(NO_TN_list)

Comments: 2163


2163

In [10]:
comments_df = pd.DataFrame(NO_TN_list, columns=['comment_id', 'submission_id', 'author', 'body', 'upvotes', 'utc_time', 'author_flair'])

In [11]:
comments_df = nfl_gamethreads.analyze_text(comments_df, text_column='body')
comments_df.sample(10).style.background_gradient()

### Variable Distributions

In [12]:
polar = alt.Chart(data=comments_df).mark_bar().encode(
    alt.X("polarity:Q", bin=True),
    y='count()'
)

subject = alt.Chart(data=comments_df).mark_bar().encode(
    alt.X("subjectivity:Q", bin=True),
    y='count()'
)

alt.hconcat(polar, subject)

alt.HConcatChart(...)

In [13]:
alt.Chart(data=comments_df).mark_bar().encode(
    alt.X("upvotes:Q", bin=True),
    y='count()'
)

alt.Chart(...)

In [14]:
alt.Chart(data=comments_df).mark_bar().encode(
    alt.X("author_flair"),
    y='count()'
)

alt.Chart(...)

In [15]:
alt.Chart(data=comments_df[comments_df['utc_time']<1636925000]).mark_line(point=True).encode(
    alt.Y("polarity:Q"),
    x='utc_time'
)

alt.Chart(...)

In [16]:
primary_fans_df = comments_df[comments_df['author_flair'].isin([':Saints: Saints', ':Titans: Titans'])]
primary_fans_df

comment_id submission_id                author  \
0       hkmff63        qtuqqs     KentuckyBourbon94   
1       hkmfulz        qtuqqs          PuddingJello   
2       hkmfxb1        qtuqqs          Theinsulated   
3       hkmffyh        qtuqqs  Successful-Client215   
4       hkmgdvr        qtuqqs        TotesMcGotes13   
...         ...           ...                   ...   
2158    hkmxk5c        qtuqqs            Never_Less   
2159    hknp28h        qtuqqs            Never_Less   
2160    hkmxfox        qtuqqs        Mr_Sarcastic12   
2161    hkn14vv        qtuqqs             No-Can946   
2162    hkn1xdn        qtuqqs        scottonetwenty   

                                                   body  upvotes  \
0     An underrated factor of playing against the Sa...       63   
1     Next year RTP calls will be reviewable but ref...       38   
2     I wish I could fuck up every aspect of my job ...       41   
3     I'm a Titans fan and these QB roughing calls a...       26   
4             Sorry Saints bros. That RTP was bullshit.       28   
...                                                 ...      ...   
2158  Ok. And they won. That is literally the only t...        1   
2159         I do appreciate you beating the Cardinals.        1   
2160                                                🤡🤡🤡        1   
2161        Just scored another, how can you not see it        1   
2162  Because Cam scoring on the Cardinals has anyth...        1   

          utc_time     author_flair  polarity  subjectivity  
0     1.636917e+09  :Titans: Titans -0.300000      0.400000  
1     1.636917e+09  :Saints: Saints -0.129365      0.171429  
2     1.636917e+09  :Saints: Saints -0.400000      0.600000  
3     1.636917e+09  :Titans: Titans -0.550000      0.533333  
4     1.636918e+09  :Titans: Titans -0.500000      1.000000  
...            ...              ...       ...           ...  
2158  1.636924e+09  :Titans: Titans  0.000000      1.000000  
2159  1.636936e+09  :Titans: Titans  0.000000      0.000000  
2160  1.636924e+09  :Titans: Titans  0.000000      0.000000  
2161  1.636925e+09  :Saints: Saints  0.000000      0.000000  
2162  1.636926e+09  :Saints: Saints -0.155556      0.288889  

[1533 rows x 9 columns]

In [17]:
alt.Chart(data=primary_fans_df).mark_bar().encode(
    alt.X("polarity:Q", bin=True),
    y='count()',
    color='author_flair',
    column='author_flair'
)

alt.Chart(...)

In [18]:
alt.Chart(data=primary_fans_df).mark_bar().encode(
    alt.X("subjectivity:Q", bin=True),
    y='count()',
    color='author_flair',
    column='author_flair'
)

alt.Chart(...)

In [19]:
alt.Chart(data=primary_fans_df[primary_fans_df['utc_time']<1636925000]).mark_line(point=True).encode(
    alt.Y("polarity:Q"),
    x='utc_time',
    color='author_flair'
)

alt.Chart(...)

In [20]:
alt.Chart(primary_fans_df).mark_point().encode(
    x='polarity:Q',
    y='subjectivity:Q',
    color='author_flair:N',
    column='author_flair:N'
)

alt.Chart(...)

## Ideas

- Which fandoms are the most/least subjective & polar?
- Which fandoms show up in rival game threads the most?
- Which fandoms show up in other game threads the most? (need to normalize for fandom population)
- If we scrape multiple years, how have variables of interest changed over time?
- Which fandoms are most negative about their own team/rival/opponent in game threads?
- What types of games are the most polarizing? Rivalry? Later in the season? Narrative explanations? In-game reasons?
- Which fandoms have the foulest mouth (filter for curse words specifically)
- Which fandoms hate the refs the most/least
- most popular words by fandom/game thread
- extract popular player names and do sentiment analysis on the subset of their relevant comments